In [10]:
import pandas as pd
import swifter

In [11]:
df = pd.read_parquet("videos.parquet")
df.head(20)

ArrowMemoryError: malloc of size 17040896 failed

In [12]:
df.video_description.isna().sum() / 2320660

0.000960933527530961

In [13]:
df['joined_text'] = df.video_title + ' ' + df.video_description
df['joined_text'] = df['joined_text'].fillna('')

In [5]:
!pip install spacy
!python -m spacy download ru_core_news_lg
!pip install umap-learn

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
     ---------------------------------------- 0.0/513.4 MB ? eta -:--:--
     ---------------------------------------- 0.2/513.4 MB 4.8 MB/s eta 0:01:47
     --------------------------------------- 1.0/513.4 MB 12.2 MB/s eta 0:00:42
     --------------------------------------- 2.7/513.4 MB 24.1 MB/s eta 0:00:22
     --------------------------------------- 5.5/513.4 MB 32.0 MB/s eta 0:00:16
      ------------------------------------- 10.1/513.4 MB 46.0 MB/s eta 0:00:11
      ------------------------------------- 12.6/513.4 MB 73.1 MB/s eta 0:00:07
     - ------------------------------------ 15.3/513.4 MB 72.6 MB/s eta 0:00:07
     - ------------------------------------ 16.9/513.4 MB 59.5 MB/s eta 0:00:09
     - ------------------------------------ 19.5/513.4 MB 50.1 MB/s eta 0:00:10
     - ------------------------------------ 21.1/51

Defaulting to user installation because normal site-packages is not writeable


In [14]:
import spacy

nlp = spacy.load("ru_core_news_lg")
text = "В видео я обывательским взглядом расскажу про монитор MSI Pro MP241X. Так же покажу решение проблемы мерцания монитора при выключенном ПК. \n!!!! АВТОР НЕ ПРЕТЕНДУЕТ НА 100% ВЕРНОСТЬ СКАЗАННЫХ СЛОВ !!!! \n\n\n\n\n\n\n#обзор #обзоры #обзорпокупок #трешобзор #юмор #монитор #гейминг #решениепроблемы #бюджетныймонитор #msi #второй_монитор #hdmi #75гц #бюджет #игры #мсай #like #subscribe \n#pc #csgo #ксго #компютер #гаджеты #мониторы #top #топчик #топ #dns #днс #blackfriday #черная_пятница #скидки #sales #скидка #fullhd #va #MSIProMP241X"
doc = nlp(text)

In [15]:
from tqdm import tqdm
tqdm.pandas()

df = df.sample(10000)
vec_df = pd.DataFrame(df.joined_text.swifter.apply(lambda x: pd.Series(nlp(x).vector)))
titles = df.category_title

Pandas Apply:   0%|          | 0/10000 [00:00<?, ?it/s]

In [ ]:
vec_df

In [178]:
import umap
from sklearn.preprocessing import PowerTransformer
from sklearn.pipeline import make_pipeline

pipe = make_pipeline(PowerTransformer())
X = pipe.fit_transform(vec_df)

# Encode the target to numeric
y_encoded = pd.factorize(df.category_title)[0]

manifold = umap.UMAP(n_components=3).fit(X, y_encoded)
X_reduced = manifold.transform(X)


In [179]:
import plotly.express as px

fig = px.scatter_3d(width=1000, height=1000, title="Эмбединг: цвет = Размеченная категория", x=X_reduced[:, 0], y=X_reduced[:, 1], z=X_reduced[: ,2], color=y_encoded, hover_name=titles)
fig.update_traces(marker_size = 2)
fig

In [147]:
titles.unique().shape

(42,)

In [152]:
from sklearn.cluster import DBSCAN, OPTICS, AgglomerativeClustering, KMeans
import plotly.express as px

# clustering = DBSCAN(eps=40, min_samples=2).fit(X)
# clustering = AgglomerativeClustering(100).fit(X)
clustering = KMeans(50).fit(X)

clusters = pd.Series(clustering.labels_)

fig = px.scatter_3d(width=1000, height=1000, title="Эмбединг: цвет = Посчитанный кластер", x=X_reduced[:, 0], y=X_reduced[:, 1], z=X_reduced[: ,2], color=clusters, hover_name=titles)
fig.update_traces(marker_size = 2)
fig

In [192]:
distances = clustering.transform(X)
calculated = pd.DataFrame(distances)
calculated.columns = [f'dist_clust_{i}' for i in range(50)]
calculated['clust'] = clusters
calculated.index = df.index

joined = pd.concat([df, calculated], axis=1)

In [194]:
joined.to_parquet('video_text_processed.parquet')